In [1]:
import os

import numpy as np
import pandas as pd
import xlrd

pd.set_option("display.max_rows", 50000)

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
fundamentals = pd.read_csv("/content/drive/MyDrive/Fiverr/PROJECT_MIMI/Fundamentals_Full.csv", na_values=' ', parse_dates=["datadate"])

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (9,25,29,916,917,919,920,926,935,937,940,941,942,943,945,955,956,959,962,965,970,978,981,984,989,992,993,997,998,1008,1009,1014,1015,1016,1017,1018,1019,1020,1021,1024,1025,1028,1029,1031,1033,1034,1035,1036,1040,1041,1042,1052,1053,1054,1055,1056,1057,1058,1059,1066,1071,1072,1074,1075,1076,1077,1081,1084,1091,1094,1096,1098,1101,1102,1103,1105,1106,1107,1108,1116,1117,1119,1120,1121,1122,1123,1124,1125,1735,1736,1737,1742,1756,1757,1762) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
ratings = pd.read_csv("/content/drive/MyDrive/Fiverr/PROJECT_MIMI/Ratings_Full.csv", na_values=' ', parse_dates=["datadate"])

In [5]:
fund_stocks = pd.read_csv("/content/drive/MyDrive/Fiverr/PROJECT_MIMI/Fund_Settlement_Security_Stocks.csv")

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (9,15,25,29,919,920,926,935,936,941,943,945,956,959,965,978,984,989,992,993,996,997,1009,1014,1015,1016,1017,1018,1019,1020,1021,1024,1025,1028,1029,1031,1033,1034,1035,1036,1041,1042,1053,1055,1056,1057,1058,1059,1066,1071,1072,1074,1075,1076,1077,1084,1091,1098,1101,1102,1103,1105,1106,1116,1119,1120,1121,1122,1124,1125,1735,1736,1737,1738,1756,1757,1762,1766) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [6]:
def excel_to_dictionary(sheetname, filename="/content/drive/MyDrive/Fiverr/PROJECT_MIMI/DataDictionary.xlsx"):
    abbreviation_dict = dict()
    
    abbreviation = xlrd.open_workbook(os.path.abspath(filename))
    abbreviation_sheet = abbreviation.sheet_by_name(sheetname)
    
    for i in range(1, abbreviation_sheet.nrows):
        abb = abbreviation_sheet.cell(i, 0).value
        abb_definition = abbreviation_sheet.cell(i, 1).value
        abbreviation_dict[abb] = abb_definition
        
    return abbreviation_dict

In [7]:
ratings_dict = excel_to_dictionary(sheetname="Ratings")
fundamentals_dict = excel_to_dictionary(sheetname="Fundamentals")

In [8]:
def rename_columns(df, df_dict):
  df.rename(columns=df_dict, inplace=True)
  df.columns = [column.lower().replace(" ", "_") for column in df.columns]
  return df

In [9]:
ratings = rename_columns(ratings, ratings_dict)
fundamentals = rename_columns(fundamentals, fundamentals_dict)

In [10]:
print("Ratings shape: {}\nFundamentals shape: {}".format(ratings.shape, fundamentals.shape))

Ratings shape: (502561, 21)
Fundamentals shape: (61429, 1768)


In [11]:
list(set(sorted(ratings.columns)) - set(sorted(fundamentals.columns)))

['s&p_subordinated_debt_rating',
 's&p_domestic_long_term_issuer_credit_rating',
 's&p_domestic_short_term_issuer_credit_rating']

In [12]:
list(set(sorted(ratings.columns)) & set(sorted(fundamentals.columns)))

['s&p_economic_sector_code',
 'company_legal_name',
 'state/province',
 'north_american_industry_classification_code',
 'ticker_symbol',
 'current_iso_country_code_-_headquarters',
 'data_date',
 'gic_sub-industries',
 'gic_industries',
 'city',
 'global_company_key',
 'standard_industry_classification_code',
 'gic_sectors',
 's&p_quality_ranking_-_current',
 'international,_domestic,_both_indicator',
 'gic_groups',
 's&p_industry_sector_code',
 'company_name']

In [13]:
# for column in list(set(sorted(ratings.columns)) - set(sorted(fundamentals.columns))):
#   ratings.loc[ratings[column].isnull(), column] = "not_rated"

In [14]:
ratings = ratings[ratings["global_company_key"].isin(list(set(ratings["global_company_key"].unique()) & set(fundamentals["global_company_key"].unique())))]
fundamentals = fundamentals[fundamentals["global_company_key"].isin(list(set(ratings["global_company_key"].unique()) & set(fundamentals["global_company_key"].unique())))]

ratings["year"] = ratings["data_date"].apply(lambda x: x.strftime("%Y"))
fundamentals["year"] = fundamentals["data_date"].apply(lambda x: x.strftime("%Y"))     
                                                                  
print("Ratings: {}\nFundamentals: {}".format(ratings.shape, fundamentals.shape))

Ratings: (362011, 22)
Fundamentals: (53671, 1769)


In [15]:
ratings[["global_company_key", "company_name"]].isnull().sum()

global_company_key    0
company_name          0
dtype: int64

In [16]:
for column in list(set(sorted(ratings.columns)) - set(sorted(fundamentals.columns))):
  ratings.loc[ratings[column].isnull(), column] = "not_recorded"

In [17]:
ratings = ratings.groupby(["global_company_key", "year", 's&p_domestic_short_term_issuer_credit_rating', 's&p_domestic_long_term_issuer_credit_rating'])[
                                        "company_name"].agg("count").reset_index()
ratings.rename(columns={"company_name": "ratings_company_count"}, inplace=True)
ratings.shape

(35743, 5)

In [18]:
# fund_rating = pd.merge(fundamentals, ratings_, on="global_company_key")
# fund_rating[fund_rating["global_company_key"] == 296944][["global_company_key", "data_date", "s&p_subordinated_debt_rating"]]

In [19]:
# pd.merge(ratings, fundamentals, on="global_company_key")

In [20]:
# fundamentals.groupby(["global_company_key", "year"])["company_name"].agg("count").reset_index()

In [21]:
ratings_constigency = pd.crosstab(ratings["s&p_domestic_long_term_issuer_credit_rating"], ratings['global_company_key'])
ratings_constigency

global_company_key                           1004    1013    ...  297209  311524
s&p_domestic_long_term_issuer_credit_rating                  ...                
A                                                 0       0  ...       0       0
A+                                                0       0  ...       0       0
A-                                                0       0  ...       0       0
AA                                                0       0  ...       0       0
AA+                                               0       0  ...       0       0
AA-                                               0       0  ...       0       0
AAA                                               0       0  ...       0       0
B                                                 0       0  ...       3       0
B+                                                0       0  ...       0       3
B-                                                0       0  ...       0       0
BB                                                5       0  ...       0       0
BB+                                               0       0  ...       0       0
BB-                                               0       0  ...       0       0
BBB                                               0       0  ...       0       0
BBB+                                              0       0  ...       0       0
BBB-                                              0       0  ...       0       0
CC                                                0       0  ...       0       0
CCC                                               0       0  ...       0       0
CCC+                                              0       0  ...       0       0
CCC-                                              0       0  ...       0       0
D                                                 0       0  ...       0       0
SD                                                0       0  ...       0       0
not_recorded                                      0       1  ...       0       0

[23 rows x 8752 columns]

In [22]:
ratings_constigency = np.power(ratings_constigency.astype("float").div(ratings_constigency.sum(axis=0), axis=1).mul(100, axis=1), 2)
ratings_constigency

global_company_key                            1004     1013    ...   297209   311524
s&p_domestic_long_term_issuer_credit_rating                    ...                  
A                                                0.0      0.0  ...      0.0      0.0
A+                                               0.0      0.0  ...      0.0      0.0
A-                                               0.0      0.0  ...      0.0      0.0
AA                                               0.0      0.0  ...      0.0      0.0
AA+                                              0.0      0.0  ...      0.0      0.0
AA-                                              0.0      0.0  ...      0.0      0.0
AAA                                              0.0      0.0  ...      0.0      0.0
B                                                0.0      0.0  ...  10000.0      0.0
B+                                               0.0      0.0  ...      0.0  10000.0
B-                                               0.0      0.0  ...      0.0      0.0
BB                                           10000.0      0.0  ...      0.0      0.0
BB+                                              0.0      0.0  ...      0.0      0.0
BB-                                              0.0      0.0  ...      0.0      0.0
BBB                                              0.0      0.0  ...      0.0      0.0
BBB+                                             0.0      0.0  ...      0.0      0.0
BBB-                                             0.0      0.0  ...      0.0      0.0
CC                                               0.0      0.0  ...      0.0      0.0
CCC                                              0.0      0.0  ...      0.0      0.0
CCC+                                             0.0      0.0  ...      0.0      0.0
CCC-                                             0.0      0.0  ...      0.0      0.0
D                                                0.0      0.0  ...      0.0      0.0
SD                                               0.0      0.0  ...      0.0      0.0
not_recorded                                     0.0  10000.0  ...      0.0      0.0

[23 rows x 8752 columns]

In [23]:
iqv = ratings_constigency.sum(axis=0).reset_index()
iqv["iqv-s&p_domestic_long_term_issuer_credit_rating"] = iqv[0].apply(lambda x: (len(ratings_constigency.index)*(np.power(100, 2) - x))/(np.power(100, 2)*(len(ratings_constigency.index) - 1)))
iqv

global_company_key  ...  iqv-s&p_domestic_long_term_issuer_credit_rating
0                   1004  ...                                         0.000000
1                   1013  ...                                         0.000000
2                   1045  ...                                         0.682746
3                   1050  ...                                         0.000000
4                   1062  ...                                         0.000000
5                   1072  ...                                         0.000000
6                   1075  ...                                         0.784091
7                   1076  ...                                         0.000000
8                   1078  ...                                         0.522727
9                   1082  ...                                         0.000000
10                  1084  ...                                         0.000000
11                  1094  ...                                         0.000000
12                  1097  ...                                         0.000000
13                  1104  ...                                         0.000000
14                  1117  ...                                         0.000000
15                  1119  ...                                         0.000000
16                  1121  ...                                         0.000000
17                  1161  ...                                         0.725417
18                  1166  ...                                         0.751420
19                  1173  ...                                         0.000000
20                  1177  ...                                         0.290404
21                  1186  ...                                         0.000000
22                  1209  ...                                         0.000000
23                  1210  ...                                         0.000000
24                  1224  ...                                         0.464646
25                  1225  ...                                         0.000000
26                  1228  ...                                         0.000000
27                  1230  ...                                         0.800224
28                  1234  ...                                         0.000000
29                  1239  ...                                         0.464646
30                  1254  ...                                         0.501818
31                  1257  ...                                         0.000000
32                  1259  ...                                         0.000000
33                  1266  ...                                         0.000000
34                  1272  ...                                         0.000000
35                  1274  ...                                         0.290404
36                  1279  ...                                         0.000000
37                  1300  ...                                         0.000000
38                  1308  ...                                         0.000000
39                  1327  ...                                         0.000000
40                  1331  ...                                         0.000000
41                  1356  ...                                         0.000000
42                  1380  ...                                         0.290404
43                  1382  ...                                         0.334545
44                  1388  ...                                         0.682746
45                  1393  ...                                         0.669091
46                  1397  ...                                         0.000000
47                  1408  ...                                         0.000000
48                  1410  ...                                         0.000000
49                  1414  ...                           

In [24]:
ratings_constigency_ = pd.crosstab(ratings["s&p_domestic_short_term_issuer_credit_rating"], ratings["global_company_key"])

In [25]:
ratings_constigency_ = np.power(ratings_constigency_.astype("float").div(ratings_constigency_.sum(axis=0), axis=1).mul(100, axis=1), 2)
ratings_constigency_

global_company_key                             1004    ...   311524
s&p_domestic_short_term_issuer_credit_rating           ...         
A-1                                               0.0  ...      0.0
A-1+                                              0.0  ...      0.0
A-2                                               0.0  ...      0.0
A-3                                               0.0  ...      0.0
B                                                 0.0  ...      0.0
B-1                                               0.0  ...      0.0
B-2                                               0.0  ...      0.0
C                                                 0.0  ...      0.0
D                                                 0.0  ...      0.0
not_recorded                                  10000.0  ...  10000.0

[10 rows x 8752 columns]

In [26]:
iqv_ = ratings_constigency_.sum(axis=0).reset_index()
iqv_["iqv-s&p_domestic_short_term_issuer_credit_rating"] = iqv_[0].apply(lambda x: (len(ratings_constigency_.index)*(np.power(100, 2) - x))/(np.power(100, 2)*(len(ratings_constigency_.index) - 1)))
iqv_

global_company_key  ...  iqv-s&p_domestic_short_term_issuer_credit_rating
0                   1004  ...                                          0.000000
1                   1013  ...                                          0.000000
2                   1045  ...                                          0.000000
3                   1050  ...                                          0.000000
4                   1062  ...                                          0.000000
5                   1072  ...                                          0.000000
6                   1075  ...                                          0.416667
7                   1076  ...                                          0.000000
8                   1078  ...                                          0.000000
9                   1082  ...                                          0.000000
10                  1084  ...                                          0.000000
11                  1094  ...                                          0.000000
12                  1097  ...                                          0.000000
13                  1104  ...                                          0.000000
14                  1117  ...                                          0.000000
15                  1119  ...                                          0.000000
16                  1121  ...                                          0.000000
17                  1161  ...                                          0.000000
18                  1166  ...                                          0.000000
19                  1173  ...                                          0.000000
20                  1177  ...                                          0.308642
21                  1186  ...                                          0.000000
22                  1209  ...                                          0.000000
23                  1210  ...                                          0.000000
24                  1224  ...                                          0.000000
25                  1225  ...                                          0.000000
26                  1228  ...                                          0.000000
27                  1230  ...                                          0.000000
28                  1234  ...                                          0.000000
29                  1239  ...                                          0.000000
30                  1254  ...                                          0.000000
31                  1257  ...                                          0.000000
32                  1259  ...                                          0.000000
33                  1266  ...                                          0.000000
34                  1272  ...                                          0.000000
35                  1274  ...                                          0.000000
36                  1279  ...                                          0.000000
37                  1300  ...                                          0.000000
38                  1308  ...                                          0.000000
39                  1327  ...                                          0.000000
40                  1331  ...                                          0.000000
41                  1356  ...                                          0.000000
42                  1380  ...                                          0.000000
43                  1382  ...                                          0.000000
44                  1388  ...                                          0.000000
45                  1393  ...                                          0.000000
46                  1397  ...                                          0.000000
47                  1408  ...                                          0.308642
48                  1410  ...                                          0.000000
49    

In [27]:
ratings = pd.merge(iqv[["global_company_key", "iqv-s&p_domestic_long_term_issuer_credit_rating"]], iqv_[["global_company_key", "iqv-s&p_domestic_short_term_issuer_credit_rating"]], on="global_company_key")

In [28]:
fund_ratings = pd.merge(fund_stocks, ratings, on="global_company_key")
fund_ratings.shape

In [29]:
fund_ratings[['price_-_close_-_daily', 'price_-_high_-_daily', 'price_-_low_-_daily', 'price_-_open_-_daily', 'price_status_code_-_daily', "global_company_key", "dividend_rate_-_monthly", 'dividends_per_share_-_ex_date_-_monthly', 'dividends_per_share_-_pay_date_-_monthly', 'common_stock_float_shares_-_canada', 'iso_currency_code_-_monthly', "settlementamount", "sued", "global_company_key", "ticker_symbol", "iqv-s&p_domestic_short_term_issuer_credit_rating", "iqv-s&p_domestic_long_term_issuer_credit_rating"]].head()

price_-_close_-_daily  ...  iqv-s&p_domestic_long_term_issuer_credit_rating
0             6949.33256  ...                                              0.0
1             6949.33256  ...                                              0.0
2             6949.33256  ...                                              0.0
3             6949.33256  ...                                              0.0
4             6949.33256  ...                                              0.0

[5 rows x 17 columns]

In [33]:
fund_ratings[fund_ratings["global_company_key"] == 1177][['price_-_close_-_daily', 'price_-_high_-_daily', 'price_-_low_-_daily', 'price_-_open_-_daily', 'price_status_code_-_daily', "global_company_key", "dividend_rate_-_monthly", 'dividends_per_share_-_ex_date_-_monthly', 'dividends_per_share_-_pay_date_-_monthly', 'common_stock_float_shares_-_canada', 'iso_currency_code_-_monthly', "settlementamount", "sued", "global_company_key", "ticker_symbol", "iqv-s&p_domestic_short_term_issuer_credit_rating", "iqv-s&p_domestic_long_term_issuer_credit_rating"]]

price_-_close_-_daily  ...  iqv-s&p_domestic_long_term_issuer_credit_rating
16              10570.928  ...                                         0.290404
17              10570.928  ...                                         0.290404
18              10570.928  ...                                         0.290404
19              10570.928  ...                                         0.290404
20              10570.928  ...                                         0.290404
21              10570.928  ...                                         0.290404
22              10570.928  ...                                         0.290404
23              10570.928  ...                                         0.290404

[8 rows x 17 columns]

In [34]:
fund_ratings.to_csv("/content/drive/MyDrive/Fiverr/PROJECT_MIMI/Fund_Settlement_Security_Stocks_Ratings.csv", index=False)